In [1]:
%matplotlib inline
import math
import openmc
import os
import shutil
import openmc.deplete
import numpy as np
import matplotlib.pyplot as plt


basedir="/home/brian/OpenMC data/Thorium/Sphere"
os.chdir(basedir)
print(os.getcwd())


/home/brian/OpenMC data/Thorium/Sphere


In [2]:

#This allows single point to change from "simple" chain file to complex chain file
#chainfile = "/home/brian/OpenMC data/chain_casl_sfr.xml"
chainfile = "/home/brian/OpenMC data/chain_simple.xml"

In [3]:
CoreRad=500.0

In [4]:
def UMaterials(materials):
    print("Total mass=",materials[0].get_mass())
    for i in materials[0].get_nuclides():
        print(i,materials[0].get_mass(i))
    print(materials[0].get_nuclide_atoms())
    return

In [5]:
def DefineMaterials(): 
    # From Design-Related Studies for the Preliminary Safety Assessment of the Molten Salt Fast Reactor
    # LiF 77.5 mol % ThF4 20% UF4 2.5% (233)
    # 
    Li=77.5
    Th=20.0
    U=2.5
    FuelSalt = openmc.Material(1,"FuelSalt")
    AtomCount=(Li*2)+(Th*5)+(U*5)
    Fl=(Li*1 +Th*4+ U*4)
    FuelSalt.set_density('g/cm3', 4.1) #
    FuelSalt.add_nuclide('Li7',   Li/AtomCount  ,'ao') 
    FuelSalt.add_nuclide('Th232', Th/AtomCount ,'ao')
    FuelSalt.add_nuclide('U233',  U /AtomCount ,'ao')
    FuelSalt.add_nuclide('F19',   Fl/AtomCount ,'ao') #=(147/247)
    FuelSalt.volume=1.0*math.pi*CoreRad*CoreRad*CoreRad/3.0   #Diameter =350 cm hieght = 350 cm 


    MatDict = {'FuelSalt':FuelSalt}
    materials=openmc.Materials([FuelSalt])
    materials.cross_sections="/home/brian/openmc/endfb-viii.0-hdf5/cross_sections.xml";
    materials.export_to_xml()
    
    return MatDict,materials


In [6]:
#Generate Basematerials.xml file
Mats, materials = DefineMaterials()
materials.export_to_xml('./Basematerials.xml')
UMaterials(materials)
Mats

Total mass= 536688744.9882563
Li7 32607936.541588247
Th232 278305014.2936866
U233 34938288.00130379
F19 190837506.15167764
{'Li7': 2.798880952476383e+30, 'Th232': 7.222918587035826e+29, 'U233': 9.028648233794782e+28, 'F19': 6.049194316642505e+30}


{'FuelSalt': Material
 	ID             =	1
 	Name           =	FuelSalt
 	Temperature    =	None
 	Density        =	4.1 [g/cm3]
 	S(a,b) Tables  
 	Nuclides       
 	Li7            =	0.2897196261682243 [ao]
 	Th232          =	0.07476635514018691 [ao]
 	U233           =	0.009345794392523364 [ao]
 	F19            =	0.6261682242990654 [ao]}

In [7]:
def DefineSettings():
    # Create a point source
    #source = openmc.Source(space=openmc.stats.Box([-5,-5,-110],[5,5,110], only_fissionable=True))
    #source = openmc.Source(space=op)
    point = openmc.stats.Point((0,0,0))
    source = openmc.Source(space=point)
    settings = openmc.Settings()
    settings.source = source
    settings.batches = 20
    settings.inactive = 10
    settings.particles = 500
    settings.temperature = { 'default':1089.0, 'method':'interpolation'}
    #1089K = 1500F
    #733K = 460C = Melting point of FLIBE, lowest temperature possible for rods to be out
    settings.export_to_xml()
    return settings

settings=DefineSettings()


In [8]:
def DefineVesselGeometry():
    CoreSphere= openmc.Sphere(r=CoreRad,boundary_type='vacuum')
    CoreCell = openmc.Cell(region=-CoreSphere, fill=Mats.get("FuelSalt"))
        
    geometry = openmc.Geometry([CoreCell])    
    geometry.export_to_xml() 

    return geometry


In [9]:
geometry=DefineVesselGeometry()

In [10]:
chain = openmc.deplete.Chain.from_xml(chainfile)
print(chain.nuclide_dict)
power = 3.0e8       #Reference Power level = 3 Gigawatts

OrderedDict([('I135', 0), ('Xe135', 1), ('Xe136', 2), ('Cs135', 3), ('Gd157', 4), ('Gd156', 5), ('U234', 6), ('U235', 7), ('U238', 8)])


In [11]:

time_steps_day=[24*60*60]*7
model = openmc.Model(geometry=geometry,materials=materials, settings=settings)
operator = openmc.deplete.Operator(model,chainfile)
integrator = openmc.deplete.PredictorIntegrator(operator, time_steps_day, power)
integrator.integrate()
results = openmc.deplete.ResultsList.from_hdf5("./depletion_results.h5")

                                %%%%%%%%%%%%%%%
                           %%%%%%%%%%%%%%%%%%%%%%%%
                        %%%%%%%%%%%%%%%%%%%%%%%%%%%%%%
                      %%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%
                    %%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%
                   %%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%
                                    %%%%%%%%%%%%%%%%%%%%%%%%
                                     %%%%%%%%%%%%%%%%%%%%%%%%
                 ###############      %%%%%%%%%%%%%%%%%%%%%%%%
                ##################     %%%%%%%%%%%%%%%%%%%%%%%
                ###################     %%%%%%%%%%%%%%%%%%%%%%%
                ####################     %%%%%%%%%%%%%%%%%%%%%%
                #####################     %%%%%%%%%%%%%%%%%%%%%
                ######################     %%%%%%%%%%%%%%%%%%%%
                #######################     %%%%%%%%%%%%%%%%%%
                 #######################     %%%%%%%%%%%%%%%%%
                 #####################

/home/brian/.local/lib/python3.10/site-packages/openmc/deplete/coupled_operator.py:542: FutureWarning: The Operator(...) class has been renamed and will be removed in a future version of OpenMC. Use CoupledOperator(...) instead.
  warn(


 Reading U233 from /home/brian/openmc/endfb-viii.0-hdf5/neutron/U233.h5
 Minimum neutron data temperature: 900 K
 Maximum neutron data temperature: 1200 K
 Preparing distributed cell instances...
 Reading plot XML file...
 Writing summary.h5 file...
[openmc.deplete] t=0.0 s, dt=86400 s, source=300000000.0
 Reading I135 from /home/brian/openmc/endfb-viii.0-hdf5/neutron/I135.h5
 Reading Xe135 from /home/brian/openmc/endfb-viii.0-hdf5/neutron/Xe135.h5
 Reading Xe136 from /home/brian/openmc/endfb-viii.0-hdf5/neutron/Xe136.h5
 Reading Cs135 from /home/brian/openmc/endfb-viii.0-hdf5/neutron/Cs135.h5
 Reading Gd157 from /home/brian/openmc/endfb-viii.0-hdf5/neutron/Gd157.h5
 Reading Gd156 from /home/brian/openmc/endfb-viii.0-hdf5/neutron/Gd156.h5
 Reading U234 from /home/brian/openmc/endfb-viii.0-hdf5/neutron/U234.h5
 Reading U235 from /home/brian/openmc/endfb-viii.0-hdf5/neutron/U235.h5
 Reading U238 from /home/brian/openmc/endfb-viii.0-hdf5/neutron/U238.h5
 Maximum neutron transport energy: 

        4/1    1.16060
        5/1    1.11074
        6/1    1.04661
        7/1    1.05896
        8/1    1.07038
        9/1    1.09081
       10/1    1.18657
       11/1    1.18074
       12/1    1.06987    1.12531 +/- 0.05543
       13/1    1.08797    1.11286 +/- 0.03434
       14/1    1.00261    1.08530 +/- 0.03673
       15/1    1.20048    1.10833 +/- 0.03661
       16/1    1.00960    1.09188 +/- 0.03412
       17/1    1.01497    1.08089 +/- 0.03086
       18/1    1.07368    1.07999 +/- 0.02674
       19/1    0.99612    1.07067 +/- 0.02536
       20/1    1.10454    1.07406 +/- 0.02293
 Creating state point statepoint.20.h5...

 =======================>     TIMING STATISTICS     <=======================

 Total time for initialization     = 0.0000e+00 seconds
   Reading cross sections          = 0.0000e+00 seconds
 Total time in simulation          = 6.2881e-01 seconds
   Time in transport only          = 6.2050e-01 seconds
   Time in inactive batches        = 3.1109e-01 seconds
 

/home/brian/.local/lib/python3.10/site-packages/openmc/deplete/helpers.py:427: RuntimeWarning: overflow encountered in scalar divide
  return source_rate / energy
/home/brian/.local/lib/python3.10/site-packages/openmc/deplete/openmc_operator.py:548: RuntimeWarning: invalid value encountered in multiply
  rates *= self._normalization_helper.factor(source_rate)
/home/brian/.local/lib/python3.10/site-packages/scipy/sparse/linalg/_dsolve/linsolve.py:276: MatrixRankWarning: Matrix is exactly singular
  warn("Matrix is exactly singular", MatrixRankWarning)


[openmc.deplete] t=604800.0 (final operator evaluation)
 Maximum neutron transport energy: 20000000 eV for F19
 Initializing source particles...

 ====================>     K EIGENVALUE SIMULATION     <====================

  Bat./Gen.      k            Average k
  =========   ========   ====================
        1/1    1.11217
        2/1    1.08411
        3/1    1.08056
        4/1    1.08239
        5/1    1.05817
        6/1    1.24909
        7/1    1.13321
        8/1    1.13662
        9/1    1.04767
       10/1    1.10143
       11/1    1.12142
       12/1    0.97640    1.04891 +/- 0.07251
       13/1    1.03986    1.04589 +/- 0.04197
       14/1    1.11770    1.06384 +/- 0.03469
       15/1    1.15749    1.08257 +/- 0.03275
       16/1    1.03753    1.07507 +/- 0.02777
       17/1    1.14693    1.08533 +/- 0.02562
       18/1    1.10807    1.08817 +/- 0.02237
       19/1    1.08315    1.08762 +/- 0.01974
       20/1    1.02903    1.08176 +/- 0.01860
 Creating state point s

AllocationError: Tally results have not been allocated yet.